In [54]:
import copy
import csv
import math
import os
from datetime import datetime
from functools import reduce
from operator import mul
import random
import collections
import numpy as np


class Flights(object):
    legNo = ""
    airport_departure = ""
    date_departure = ""
    hour_departure = ""
    airport_arrival = ""
    date_arrival = ""
    hour_arrival = ""
    pairing_relation = ""
    date_time_arrival = None
    date_time_departure = None
    duration = 0

    # deadhead = False

    def __int__(self):
        self.legNo = self.legNo
        self.airport_departure = self.airport_departure
        self.date_departure = self.date_departure
        self.hour_departure = self.hour_departure
        self.airport_arrival = self.airport_arrival
        self.date_arrival = self.date_arrival
        self.hour_arrival = self.hour_arrival
        self.pairing_relation = self.pairing_relation

    def setDateTime(self):
        self.date_time_departure = datetime.strptime(str(self.date_departure + ' ' + self.hour_departure), "%Y-%m-%d "
                                                                                                           "%H:%M")
        self.date_time_arrival = datetime.strptime(str(self.date_arrival + ' ' + self.hour_arrival), "%Y-%m-%d %H:%M")
        diff = self.date_time_arrival - self.date_time_departure
        seconds_in_hours = diff.seconds / 60 / 60
        days_in_hours = diff.days * 24
        self.duration = seconds_in_hours + days_in_hours

    def __eq__(self, other):
        return self.legNo == other.legNo

    def __hash__(self):
        return hash(('legNo', self.legNo))


class Duties(object):
    legs: list[Flights] = []
    start_date_time = None
    end_date_time = None
    starting_airport = ""
    ending_airport = ""
    total_flying_time = 0
    total_duration = 0

    def __init__(self, legs: list[Flights]):
        self.legs = legs
        self.start_date_time = legs[0].date_time_departure
        self.end_date_time = legs[-1].date_time_arrival
        self.starting_airport = legs[0].airport_departure
        self.ending_airport = legs[-1].airport_arrival
        dur = 0.0
        for l3g in legs:
            dur += (l3g.date_time_arrival-l3g.date_time_departure).total_seconds()/60/60
        self.total_flying_time = dur
        self.total_duration = (self.end_date_time - self.start_date_time).total_seconds() / 60 / 60

        # if self.total_flying_time > self.total_duration:
        #     for l3g in legs:
        #         print((l3g.date_time_arrival-l3g.date_time_departure).total_seconds()/60/60)
        #     print(self.end_date_time, self.start_date_time)

class Pairings(object):
    legs: list[Flights] = []
    start_date_time = None
    end_date_time = None
    base_airport = ""
    total_duration = 0
    total_flying_time = 0
    cost = 0

    def __init__(self, duties: list[Duties]):
        self.legs = []
        for dty in duties:
            for l3g in dty.legs:
                self.legs.append(l3g)
            self.total_flying_time += dty.total_flying_time
        self.start_date_time = duties[0].start_date_time
        self.end_date_time = duties[-1].end_date_time
        self.base_airport = duties[0].starting_airport
        # self.total_flying_time = reduce(mul, [x.total_flying_time for x in duties])
        self.total_duration = (self.end_date_time - self.start_date_time).total_seconds() / 60 / 60

    def __eq__(self, other):
        return self.legs == other.legs

In [55]:
def searchForDuties(current: [], duties: []):
    keepDuty, cont = validDuty(current)
    if keepDuty == 1:
        d = Duties(copy.deepcopy(current))
        duties.append(d)
    if cont == 1:
        last: Flights = current[-1]
        for laterLeg in flights:
            if laterLeg.airport_departure == last.airport_arrival and last.date_time_arrival < laterLeg.date_time_departure:
                current.append(laterLeg)
                searchForDuties(current, duties)
                current.remove(laterLeg)
    return duties

In [56]:
def validDuty(current: list[Flights]):
    # constraints:
    # start and end at same base
    # is there enough time between each leg (20 minutes
    # has the flight been going on for a number of hours (8)
    # a duty cannot have an intermediate stop in a hub airport
    keepDuty = 1
    cont = 1
    duration = 0
    # if len(current) < 2:
    #     keep = 0

    if current[0].date_departure != current[-1].date_departure:
        cont = 0
        keepDuty = 0

    if current[-1].date_departure != current[-1].date_arrival:
        cont = 0

    for i, v in enumerate(current):
        duration += v.duration
        if i + 1 != len(current) and keepDuty == 1:
            if (current[i + 1].date_time_departure - v.date_time_arrival).total_seconds() / 60 < 20:
                keepDuty = 0
                cont = 0
                break

    if duration > 8:
        keepDuty = 0
        cont = 0

    # if current[0].airport_departure == current[-1].airport_arrival:
    #     cont = 0

    return keepDuty, cont


In [57]:
# A cost function to determine what passes and what stays
# must also check if all legs are covered
# could do this after each - delete them if they have a ratio of flying time to duty time of less than 0.5 (example)

def searchForPairings(current: [], pairings: [], stop):
    current: list[Duties]
    keepPairing, cont = validPairing(current)
    if keepPairing == 1:
        p = Pairings(copy.deepcopy(current))
        pairings.append(p)
        print(len(pairings))
        if len(pairings) >= 100:
            stop = True
    if cont == 1:
        last: Duties = current[-1]
        index = all_duties.index(last)
        # to optimise we can split duties by airport AND sort by time, that way we can search for all the duties
        # starting after x time therefore optimising it
        for duty in all_duties[index:]:
            if (duty.end_date_time - current[0].start_date_time).total_seconds() / 60 / 60 / 24 > 3 or stop:
                break
            if last.ending_airport == duty.starting_airport and last.end_date_time < duty.start_date_time:
                current.append(duty)
                stop, pairings = searchForPairings(current, pairings, stop)
                current.remove(duty)
    return stop, pairings


In [58]:
def validPairing(current: list[Duties]):
    # cannot be longer than 3 days.
    # Can have layovers of up to 10 hours as long as there are flights that would be
    # back before the 3 day mark (therefore only 2 layovers possible)
    # starts and ends at the same airport
    tempP = Pairings(current)
    keepPairing = 1
    cont = 1

    # total_pairing_duration = 0
    layover_timer = 0

    if current[0].starting_airport.find("BASE") == -1 or tempP.total_duration / 24 > 3:
        keepPairing = 0
        cont = 0
    # elif tempP.total_flying_time/tempP.total_duration * 100 < 50:
    #     keep = 0
    #     cont = 0
    else:
        if current[0].starting_airport != current[-1].ending_airport:
            keepPairing = 0

        for i, v in enumerate(current):
            v: Duties
            if i + 1 != len(current):
                duty_diff = (current[i + 1].start_date_time - v.end_date_time).total_seconds() / 60
                layover_timer += (current[i + 1].start_date_time - v.start_date_time).total_seconds() / 60 / 60
                if duty_diff < 20:
                    keepPairing = 0
                    cont = 0
                    break
                    #This isnt checking for layovers properly

                if duty_diff / 60 > 10:
                    layover_timer = 0

                if layover_timer > 8:
                    keepPairing = 0
                    cont = 0
                    break

    if cont and keepPairing:
        chance = random.random()
        if chance > 0.9:
            cont = 0
    return keepPairing, cont


# def calcDutyCost(duty):
#     cost = 0
#     return cost


In [59]:
def calcPairingCost(pair: Pairings):
    num_legs = len(pair.legs)
    TAFB = pair.total_duration
    total_duty_cost = max([0, TAFB * 4 / 7, pair.total_flying_time])
    cost = max([num_legs * 5, TAFB * 2 / 7, total_duty_cost])
    return cost


In [60]:
def flush(cd: {}):
    for key in cd.keys():
        cd[key] = (False, 0)

    # return collections.OrderedDict(sorted(cd))


In [61]:
def checkCovered(cvd):
    cov = True
    for it in cvd.items():
        if not it[1][1]:
            print(it)
            cov = False
    return cov

In [63]:
flights: list[Flights] = []
covered = {}
# global all_pairings
for day in range(31):
    path = os.getcwd() + '\instance1\day_' + str(day + 1) + '.csv'
    first = True
    with open(path) as csv_file:
        reader = csv.reader(csv_file, delimiter=',')
        for row in reader:
            if not row:
                continue
            elif first:
                first = False
                continue
            elif len(row) <= 6:
                continue
            else:
                f = Flights()
                f.legNo = row[0].strip()
                f.airport_departure = row[1].strip()
                f.date_departure = row[2].strip()
                f.hour_departure = row[3].strip()
                f.airport_arrival = row[4].strip()
                f.date_arrival = row[5].strip()
                f.hour_arrival = row[6].strip()
                key = str(f.legNo.strip())
                covered[key] = (False, 0)
                f.setDateTime()
                flights.append(f)
# flights.pop(0)

In [64]:
# print()
all_duties: list[Duties] = []
legal_leg_duties = {}
for leg in flights:
    new_duties = searchForDuties([leg], [])
    # print(len(new_duties))
    for duty in new_duties:
        # for duty in all_duties:
        ratio = duty.total_flying_time / duty.total_duration * 100
        if ratio < 50:
            new_duties.remove(duty)
            # print("Hit")
        else:
            for legs in duty.legs:
                if legs.legNo not in legal_leg_duties:
                    legal_leg_duties[legs.legNo] = []
                legal_leg_duties[legs.legNo].append(duty)
    # print(len(new_duties))
    all_duties.extend(new_duties)

all_duties.sort(key=lambda x: x.start_date_time, reverse=False)

# for duty in all_duties:
#     display = ""
#     for i, duty_legs in enumerate(duty.legs):
#         display += duty_legs.legNo
#
#         if i + 1 != len(duty.legs):
#             display += "->"
#     print(display, "\n--------------")

print("Total Legal Duties:", len(all_duties))

Total Legal Duties: 6860


In [65]:
all_duties

 ...]

In [66]:
# Intractable we need to find a better way
# for duty in all_duties:
#     new_pairings = searchForPairings([duty], [])
#     all_pairings.extend(new_pairings)

all_pairings: list[Pairings] = []
all_covered = False
legal_pairings_by_leg = {}
for leg in flights:
    stop = False
    random_duty = legal_leg_duties[leg.legNo][random.randint(0, len(legal_leg_duties[leg.legNo]) - 1)]
    _, new_pairings = searchForPairings([random_duty], [], stop)
    for pair in new_pairings:
        for legs in pair.legs:
            covered[legs.legNo] = (True, covered[legs.legNo][1] + 1)
    all_pairings.extend(new_pairings)
    print(leg.legNo)

print("Uncovered:")
for item in covered.items():
    if not item[0]:
        print(item)
print("-------------")

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
LEG_01_0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
LEG_01_1
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
LEG_01_2
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
3

In [67]:
base1 = []
base2 = []
base3 = []

for pairing in all_pairings:
    if pairing.base_airport == "BASE1":
        base1.append(pairing)
    elif pairing.base_airport == "BASE2":
        base2.append(pairing)
    elif pairing.base_airport == "BASE3":
        base3.append(pairing)
print(len(all_pairings))

34351


In [68]:
# optimise to only check within same base
print("bef:", len(all_pairings))
for i, val1 in enumerate(all_pairings):
    # print(i)
    already_found = False
    if val1.base_airport == "BASE1":
        for j, val2 in enumerate(base1):
            if val1.legs == val2.legs and already_found:
                all_pairings.remove(val1)
                print("hit")
                break
            if val1 == val2:
                already_found = True
    elif val1.base_airport == "BASE2":
        for j, val2 in enumerate(base2):
            if val1.legs == val2.legs and already_found:
                all_pairings.remove(val1)
                print("hit")
                break
            if val1 == val2:
                already_found = True
    elif val1.base_airport == "BASE3":
        for j, val2 in enumerate(base3):
            if val1.legs == val2.legs and already_found:
                all_pairings.remove(val1)
                print("hit")
                break
            if val1 == val2:
                already_found = True

print("aft;", len(all_pairings))

bef: 34351
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
hit
h

In [69]:
for i, pairing in enumerate(all_pairings):
    pairing: Pairings
    display = ""
    for leg in pairing.legs:
        display += leg.legNo + "->"
    print("Pairing ", i + 1, ": ", display[:len(display) - 2], sep="")
    print("Total Time:", pairing.total_duration)
    print("Total Flying Time:", pairing.total_flying_time)
    print("--------------")
print("Total Pairings:", len(all_pairings))

Pairing 1: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_01_33->LEG_02_3->LEG_02_2->LEG_02_21->LEG_02_4->LEG_03_3->LEG_03_2->LEG_03_26->LEG_03_16
Total Time: 56.9
Total Flying Time: 17.56666666666667
--------------
Pairing 2: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_01_33->LEG_02_3->LEG_02_2->LEG_02_21->LEG_02_4->LEG_03_26->LEG_03_16
Total Time: 56.9
Total Flying Time: 13.916666666666668
--------------
Pairing 3: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_01_33->LEG_02_3->LEG_02_2->LEG_02_21->LEG_02_4->LEG_02_5->LEG_03_7->LEG_03_26->LEG_03_16
Total Time: 56.9
Total Flying Time: 16.200000000000003
--------------
Pairing 4: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_01_33->LEG_02_3->LEG_02_2->LEG_02_21->LEG_02_4->LEG_02_33->LEG_03_10
Total Time: 50.5
Total Flying Time: 16.683333333333334
--------------
Pairing 5: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_01_33->LEG_02_3->LEG_02_2->LEG_02_26->LEG_02_16
Total Time: 32.9
Total Flyi

In [73]:
#Remove pairings where the flying time to duration ratio is less than 70%

orig = copy.deepcopy(all_pairings)
len(orig)
for i, pairing in enumerate(orig):
    if i == 3054:
        print()
    if pairing.total_flying_time/pairing.total_duration * 100 < 30:
        all_pairings.remove(pairing)
len(all_pairings)

9412

In [74]:
flush(covered)
for pair in all_pairings:
    for legs in pair.legs:
        covered[legs.legNo] = (True, covered[legs.legNo][1] + 1)
covered

{'LEG_01_0': (True, 30),
 'LEG_01_1': (True, 30),
 'LEG_01_2': (True, 99),
 'LEG_01_3': (True, 128),
 'LEG_01_4': (True, 77),
 'LEG_01_5': (True, 132),
 'LEG_01_6': (True, 51),
 'LEG_01_8': (True, 51),
 'LEG_01_9': (True, 51),
 'LEG_01_11': (True, 10),
 'LEG_01_12': (True, 44),
 'LEG_01_14': (False, 0),
 'LEG_01_15': (True, 54),
 'LEG_01_16': (True, 1),
 'LEG_01_17': (False, 0),
 'LEG_01_18': (True, 136),
 'LEG_01_19': (True, 82),
 'LEG_01_20': (True, 54),
 'LEG_01_21': (True, 77),
 'LEG_01_23': (True, 82),
 'LEG_01_25': (True, 38),
 'LEG_01_26': (True, 43),
 'LEG_01_28': (True, 64),
 'LEG_01_29': (True, 82),
 'LEG_01_30': (True, 64),
 'LEG_01_31': (True, 99),
 'LEG_01_32': (True, 96),
 'LEG_01_33': (True, 170),
 'LEG_02_0': (True, 97),
 'LEG_02_1': (True, 127),
 'LEG_02_2': (True, 102),
 'LEG_02_3': (True, 102),
 'LEG_02_4': (True, 66),
 'LEG_02_5': (True, 87),
 'LEG_02_6': (True, 172),
 'LEG_02_7': (True, 176),
 'LEG_02_8': (True, 172),
 'LEG_02_9': (True, 98),
 'LEG_02_10': (True, 9

In [21]:
for i, pairing in enumerate(all_pairings):
    pairing: Pairings
    display = ""
    for leg in pairing.legs:
        display += leg.legNo + "->"
    print("Pairing ", i + 1, ": ", display[:len(display) - 2], sep="")
    print("Total Time:", pairing.total_duration)
    print("Total Flying Time:", pairing.total_flying_time)
    print("--------------")
print("Total Pairings:", len(all_pairings))

Pairing 1: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_02_16->LEG_02_17->LEG_03_13
Total Time: 52.81666666666667
Total Flying Time: 11.416666666666668
--------------
Pairing 2: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_02_34->LEG_03_25->LEG_03_27->LEG_03_26->LEG_03_16
Total Time: 56.9
Total Flying Time: 13.316666666666666
--------------
Pairing 3: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_02_34->LEG_03_3->LEG_03_2->LEG_03_26->LEG_03_16
Total Time: 56.9
Total Flying Time: 11.45
--------------
Pairing 4: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_02_34->LEG_02_5->LEG_03_7->LEG_03_26->LEG_03_16
Total Time: 56.9
Total Flying Time: 10.083333333333332
--------------
Pairing 5: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_02_34->LEG_02_33->LEG_03_10
Total Time: 50.5
Total Flying Time: 10.566666666666668
--------------
Pairing 6: LEG_01_0->LEG_01_1->LEG_01_31->LEG_01_2->LEG_01_3->LEG_01_33->LEG_02_3->LEG_02_2->LEG_02_31->LEG_02_0->LEG_

In [ ]:
covered = flush(covered)
max_weight = -1
min_weight = 100000000

In [ ]:
for pairing in all_pairings:
    pairing.cost = calcPairingCost(pairing)
    if pairing.cost > max_weight:
        max_weight = pairing.cost
    if pairing.cost < min_weight:
        min_weight = pairing.cost

all_pairings.sort(key=lambda x: x.cost, reverse=True)

cum_weigh = [x for x in range(0, len(all_pairings))]

kept_pairings: list[Pairings] = []

iterations = 0


In [ ]:
while (not all_covered) and iterations < 500:
    iterations += 1
    p: Pairings = random.choices(all_pairings, weights=cum_weigh, k=1)[0]
    keep = True
    if p not in kept_pairings:
        for l in p.legs:
            # covered[l.legNo] = (True, covered[l.legNo] + 1)  # check for repeated leg coverings <--  Todo imp
            if covered[l.legNo] and covered[l.legNo][1] > 2:
                keep = False

        if keep:
            for l in p.legs:
                covered[l.legNo] = (True, covered[l.legNo][1] + 1)
            kept_pairings.append(p)

    all_covered = checkCovered(covered)

print(checkCovered(covered))
# choose one randomly from pairing starting with particular leg